# Modular PPO Pipeline for Atari Warlords

In [3]:
%%html
<div style="font-family: 'Courier New', Courier, monospace; max-width: 500px; margin: 20px auto; padding: 20px; border: 3px solid #39ff14; border-radius: 12px; background: #1a1a1a; box-shadow: 0 0 15px #39ff14;">
  <h2 style="text-align: center; color: #ff073a; margin-bottom: 1em; text-shadow: 0 0 8px #ff073a;">Autonomous Systems</h2>

  <ul style="list-style-type: none; padding: 0; margin-bottom: 1.5em; font-size: 1.1em;">
    <li style="color: #39ff14; padding: 6px 0; border-bottom: 1px solid #444;">
      <strong>Jasper Duncker</strong> <span style="float:right; color: #ff073a;">18014445</span>
    </li>
    <li style="color: #39ff14; padding: 6px 0; border-bottom: 1px solid #444;">
      <strong>Busse Heemskerk</strong> <span style="float:right; color: #ff073a;">22122877</span>
    </li>
    <li style="color: #39ff14; padding: 6px 0; border-bottom: 1px solid #444;">
      <strong>Natasja de Kok</strong> <span style="float:right; color: #ff073a;">22059326</span>
    </li>
    <li style="color: #39ff14; padding: 6px 0;">
      <strong>Tim Oosterling</strong> <span style="float:right; color: #ff073a;">22078800</span>
    </li>
  </ul>

  <div style="color: #39ff14; font-size: 1em; line-height: 1.5; text-shadow: 0 0 6px #39ff14;">
    <p><strong>Datum:</strong> <span style="color: #ff073a;">20 juni 2025</span></p>
    <p><strong>Vak:</strong> <span style="color: #ff073a;">Autonomous Systems</span></p>
    <p><strong>Docent:</strong> <span style="color: #ff073a;">Vikram Radhakrishnan</span></p>
    <p><strong>Instituut:</strong> <span style="color: #ff073a;">Haagse Hogeschool</span></p>
  </div>
</div>


### Installeren
Necessary installs

In [ ]:
%pip install pettingzoo[atari]
%pip install "autorom[accept-rom-license]"
%pip install --find-links dist/ --no-cache-dir AutoROM[accept-rom-license]
!pip install supersuit
!pip install stable_baselines3
!pip install --upgrade "supersuit>=3.5.0"



Looking in links: dist/


### Import statements

In [ ]:
#NKOK AutoROM aan de praat krijgen

In [ ]:
# Start AutoROM

# !AutoROM

# Import libraries
from pettingzoo.atari import warlords_v3
from pettingzoo.utils import BaseParallelWrapper
import gymnasium as gym
import numpy as np
from collections import defaultdict, Counter
import importlib
import os
import imageio
import supersuit as ss
from stable_baselines3 import PPO
from stable_baselines3.common.vec_env import VecMonitor, VecFrameStack
from pettingzoo.utils.conversions import aec_to_parallel
import time

### Hulpcode voor AutoROM

De code runde niet op alle laptops van de projectgenoten hetzelfde. Bij de laptop van Natasja bijvoorbeeld was deze extra code nodig om AutoROM werkend te krijgen. Het script accepteert automatisch de licentie van AutoROM en zoekt vervolgens in de map /root/.local/share/ naar bestanden waarvan de naam "warlords" bevat. Daarna print het een lijst met de volledige paden van die bestanden.

In [ ]:
#NKOK: anders deed AutoROM het niet
!AutoROM --accept-license

import os
print([os.path.join(dp, f) for dp, dn, filenames in os.walk("/root/.local/share/") for f in filenames if "warlords" in f.lower()])


AutoROM will download the Atari 2600 ROMs.
They will be installed to:
	/usr/local/lib/python3.11/dist-packages/AutoROM/roms
	/usr/local/lib/python3.11/dist-packages/multi_agent_ale_py/roms

Existing ROMs will be overwritten.
[]


## Modeltraining

Hieronder worden een aantal agents getraind, met verschillende doeleinden. Sommige codeblocks zijn van experimentele aard.

### Modeltraining: simpel model 1

Zorgt voor parallel processing. Initialiseert de pettingzoo omgeving Atari en zorgt voor wrappers die agents die er niet meer zijn niet meer worden meegerekend, acties maar eens in de 4 keer laat gebeuren (frame_skip van 4), het omzetten naar het juiste inputtype, namelijk float32 en normalisatie. Vectoriseert de environment, zodat het runnen van paralelle omgevingen mogelijk is met Stable Baselines 3.


In [ ]:
#Code 1 Jasper
import numpy as np
import supersuit as ss
from pettingzoo.atari import warlords_v3
from stable_baselines3.common.vec_env import VecMonitor, VecTransposeImage

def make_env(num_envs=4):
    # 1. Init environment
    env = warlords_v3.env(render_mode="rgb_array")

    # 2. Convert to parallel (for multi-agent)
    env = aec_to_parallel(env)



    # 3. Add wrappers
    env = ss.black_death_v3(env)  # Mask dead agents
    env = ss.frame_skip_v0(env, 4)  # Frame skipping (default in Atari)
    env = ss.dtype_v0(env, np.float32)  # Convert to float32
    env = ss.normalize_obs_v0(env, env_min=0, env_max=255)  # Normalize pixel values

    # 4. Convert to vectorized environment for SB3
    env = ss.pettingzoo_env_to_vec_env_v1(env)

    # 5. Run multiple copies in parallel (same agent logic reused)
    env = ss.concat_vec_envs_v1(env, num_vec_envs=num_envs, num_cpus=1, base_class="stable_baselines3")

    # 6. Reorder image axes to channel-first [C,H,W], needed for MlpPolicy
    #env = ss.flatten_v0(env)

    # 7. Optional: Monitor for logging
    env = VecMonitor(env)

    return env





"""env = make_env(num_envs=2)
model = PPO("MlpPolicy", env, verbose=1)
model.learn(total_timesteps=1_000_000, progress_bar=True)
model.save("warlords_parallel_model.zip")
"""


#Comments weggehaald om te trainen NKOK
env = make_env(num_envs=2)
model = PPO("MlpPolicy", env, verbose=1) #hyperparameters
model.learn(total_timesteps=1_000_000, progress_bar=True) #hyperparameters
model.save("warlords_parallel_model.zip")


/usr/local/lib/python3.11/dist-packages/stable_baselines3/common/vec_env/base_vec_env.py:78: UserWarning: The `render_mode` attribute is not defined in your environment. It will be set to None.
  warnings.warn("The `render_mode` attribute is not defined in your environment. It will be set to None.")


Using cuda device


Output()

/usr/local/lib/python3.11/dist-packages/ipywidgets/widgets/widget_output.py:111: DeprecationWarning: 
Kernel._parent_header is deprecated in ipykernel 6. Use .get_parent()
  if ip and hasattr(ip, 'kernel') and hasattr(ip.kernel, '_parent_header'):

/usr/local/lib/python3.11/dist-packages/stable_baselines3/common/on_policy_algorithm.py:150: UserWarning: You are trying to run PPO on the GPU, but it is primarily intended to run on the CPU when not using a CNN policy (you are using ActorCriticPolicy which should be a MlpPolicy). See https://github.com/DLR-RM/stable-baselines3/issues/1245 for more info. You can pass `device='cpu'` or `export CUDA_VISIBLE_DEVICES=` to force using the CPU.Note: The model will train, but the GPU utilization will be poor and the training might take longer than on CPU.
  warnings.warn(


KeyboardInterrupt: 

!pip install optuna

In [ ]:
# !pip install optuna

### Hyperparameters vinden met Optuna: kleine schaal (gelukt)

Nog een experiment, waarbij er werd gedaan aan hyperparameter search door middel van Optuna. Door het beperkte aantal total_timesteps, trials en parameters dat wordt gebruikt door Optuna ligt hier nog ruimte voor verbetering. Verder is er gebruik gemaakt van diverse wrappers. Er zijn meer hyperparameters dan in de vorige trainingscode. De learning rate bepaalt hoe groot de updates zijn met een clipping range die de update ook nog verkleint, de gamma zegt iets over hoezeer de  expected values meetellen van toekomstige stappen en de ent_coef geeft de entropiecoefficient, oftewel hoezeer de agent wordt aangespoord om aan exploratie (onzekerheid in acties) te doen. Door middel van Optuna kunnen hier de beste waarden van worden gezocht.
Wat verder nog van belang is is dat er code in staat die het geheugen opschonen, zodat dat niet volloopt. Die code zorgt ervoor dat het gebruikte geheugen van het model en de omgeving wordt vrijgegeven. Hierdoor voorkomt het dat het geheugen vol raakt en de computer vertraagt of crasht. Dit is met name een probleem als het wordt gerund in de gratis versie van Colab.
Een probleem met de uitkomsten van de volgende code was dat er geen goede prestaties zijn behaald. De beloning was maximaal 0. Daarop heb ik daarom code uitgeprobeerd om te kijken of het aan het model lag. Maar het model haalde wel gewoon een positieve score, dus dat was het niet. Wij denken dat het ligt aan dat we de beloning niet goed konden aanpassen.



In [ ]:
#EXPERIMENT NKOK1: runde wel.
#Code 1 Jasper: NKOK Optuna (en bijhouden hoe lang het duurt)
# stap 1 Bij n_trials=5 gaf hij bij trial 1 een beloning van 0 en daarna negatieve gemiddelde beloning van -0.5.
# maar toen liep hij vast qua RAM dus ik ben van 20.000 -> 10.000 total_timesteps gegaan. Ook heb ik code toegevoegd om VRAM vrij te maken:
"""
Hij ruimt het model, de omgeving (env) en de GPU-geheugen-cache (torch.cuda.empty_cache()) expliciet op door
ze te verwijderen en de garbage collector (gc.collect()) en torch.cuda.empty_cache() aan te roepen om geheugen vrij te maken na elke trial.
"""
#Het beloningsmodel werkt wel, (zie de cel hierboven), dus ik moest wat aanpassen.

import time
import sys
import optuna
import numpy as np
import supersuit as ss
from pettingzoo.atari import warlords_v3
from stable_baselines3 import PPO
from stable_baselines3.common.vec_env import VecMonitor
from stable_baselines3.common.evaluation import evaluate_policy
from pettingzoo.utils.conversions import aec_to_parallel
import gc
import torch  # alleen als je GPU gebruikt

def make_env(num_envs=1): #wrappers
    env = warlords_v3.env(render_mode="rgb_array")
    env = aec_to_parallel(env)
    env = ss.black_death_v3(env)
    env = ss.frame_skip_v0(env, 4)
    env = ss.dtype_v0(env, np.float32)
    env = ss.normalize_obs_v0(env, env_min=0, env_max=255)
    env = ss.pettingzoo_env_to_vec_env_v1(env)
    env = ss.concat_vec_envs_v1(env, num_vec_envs=num_envs, num_cpus=1, base_class="stable_baselines3")
    env = VecMonitor(env)
    return env

def objective(trial):
    print(f"\n=== Start trial {trial.number} ===")
    sys.stdout.flush()

    learning_rate = trial.suggest_loguniform('learning_rate', 1e-5, 1e-3)
    gamma = trial.suggest_uniform('gamma', 0.9, 0.9999)
    ent_coef = trial.suggest_loguniform('ent_coef', 1e-8, 1e-2)
    clip_range = trial.suggest_uniform('clip_range', 0.1, 0.4)

    env = make_env(num_envs=1)

    model = PPO("MlpPolicy", env,   #hyperparameters
                learning_rate=learning_rate,
                gamma=gamma,
                ent_coef=ent_coef,
                clip_range=clip_range,
                verbose=1)

    model.learn(total_timesteps=10_000, progress_bar=True)
    mean_reward, _ = evaluate_policy(model, env, n_eval_episodes=5, warn=False)
    env.close()

    #oplossing vollopen
    del model
    del env
    gc.collect()
    if torch.cuda.is_available():
        torch.cuda.empty_cache()

    print(f"Trial {trial.number} klaar. Gemiddelde reward: {mean_reward:.2f}")
    sys.stdout.flush()

    return mean_reward

start = time.time()
study = optuna.create_study(direction="maximize")
study.optimize(objective, n_trials=5, catch=(Exception,))

print("\n=== Resultaten ===")
print("Beste hyperparameters:", study.best_params)
print("Beste reward:", study.best_value)
print(f"Totaaltijd: {time.time() - start:.2f} seconden")


[I 2025-06-21 21:07:38,840] A new study created in memory with name: no-name-61e40740-03ed-4205-847c-c2f4724e0058



=== Start trial 0 ===


/tmp/ipython-input-1-4042915338.py:38: FutureWarning: suggest_loguniform has been deprecated in v3.0.0. This feature will be removed in v6.0.0. See https://github.com/optuna/optuna/releases/tag/v3.0.0. Use suggest_float(..., log=True) instead.
  learning_rate = trial.suggest_loguniform('learning_rate', 1e-5, 1e-3)
/tmp/ipython-input-1-4042915338.py:39: FutureWarning: suggest_uniform has been deprecated in v3.0.0. This feature will be removed in v6.0.0. See https://github.com/optuna/optuna/releases/tag/v3.0.0. Use suggest_float instead.
  gamma = trial.suggest_uniform('gamma', 0.9, 0.9999)
/tmp/ipython-input-1-4042915338.py:40: FutureWarning: suggest_loguniform has been deprecated in v3.0.0. This feature will be removed in v6.0.0. See https://github.com/optuna/optuna/releases/tag/v3.0.0. Use suggest_float(..., log=True) instead.
  ent_coef = trial.suggest_loguniform('ent_coef', 1e-8, 1e-2)
/tmp/ipython-input-1-4042915338.py:41: FutureWarning: suggest_uniform has been deprecated in v3.0.

Using cuda device


Output()

...

Output()

---------------------------------
| rollout/           |          |
|    ep_len_mean     | 1.76e+03 |
|    ep_rew_mean     | -0.5     |
| time/              |          |
|    fps             | 430      |
|    iterations      | 1        |
|    time_elapsed    | 19       |
|    total_timesteps | 8192     |
---------------------------------
-----------------------------------------
| rollout/                |             |
|    ep_len_mean          | 1.6e+03     |
|    ep_rew_mean          | -0.5        |
| time/                   |             |
|    fps                  | 260         |
|    iterations           | 2           |
|    time_elapsed         | 62          |
|    total_timesteps      | 16384       |
| train/                  |             |
|    approx_kl            | 0.010093044 |
|    clip_fraction        | 0.015       |
|    clip_range           | 0.253       |
|    entropy_loss         | -1.78       |
|    explained_variance   | -0.93       |
|    learning_rate        | 0.

Trial 4 klaar. Gemiddelde reward: -0.20


[I 2025-06-21 21:22:37,344] Trial 4 finished with value: -0.20000000298023224 and parameters: {'learning_rate': 0.00014415072236570735, 'gamma': 0.9714201272814482, 'ent_coef': 0.0018742554890183883, 'clip_range': 0.2533979086349173}. Best is trial 1 with value: 0.0.



=== Resultaten ===
Beste hyperparameters: {'learning_rate': 9.073856487190843e-05, 'gamma': 0.9914029026872296, 'ent_coef': 2.6214567878199265e-06, 'clip_range': 0.3654176142820331}
Beste reward: 0.0
Totaaltijd: 898.51 seconden


In [ ]:
#NKOK toegevoegd: Het onderstaande experiment werkte niet, dus ik ging kijken of beloningen uberhaupt wel mogelijk waren.
import gymnasium as gym
from stable_baselines3 import PPO
from stable_baselines3.common.evaluation import evaluate_policy

env = gym.make("CartPole-v1")  # gymnasium gebruikt dezelfde naam
model = PPO("MlpPolicy", env, verbose=0)
mean_reward, _ = evaluate_policy(model, env, n_eval_episodes=5, warn=False)
print(f"Ongetraind model gemiddelde reward: {mean_reward}")


Ongetraind model gemiddelde reward: 71.4


### Hyperparameters vinden met Optuna: grotere schaal schaal (vastgelopen)

Deze code vormt een voortzetting van de vorige codecel, maar dan met een grotere hoeveelheid timesteps en trials. Er was helaas niet genoeg tijd om deze code helemaal af te maken, want de code die in de nacht runde was vastgelopen bij trial nummer 8, ondanks het geheugen-verversingsmechanisme uit de code.

In [ ]:
##EXPERIMENT NKOK2
#door nacht runnen nkok
#Code 1 Jasper: NKOK Optuna (en bijhouden hoe lang het duurt)
# stap 1 Bij n_trials=5 gaf hij bij trial 1 een beloning van 0 en daarna negatieve gemiddelde beloning van -0.5.
# maar toen liep hij vast qua RAM dus ik ben van 20.000 -> 10.000 total_timesteps gegaan. Ook heb ik code toegevoegd om VRAM vrij te maken:
"""
Hij ruimt het model, de omgeving (env) en de GPU-geheugen-cache (torch.cuda.empty_cache()) expliciet op door
ze te verwijderen en de garbage collector (gc.collect()) en torch.cuda.empty_cache() aan te roepen om geheugen vrij te maken na elke trial.
"""
#Het beloningsmodel werkt wel, (zie de cel hierboven), dus ik moest wat aanpassen.

import time
import sys
import optuna
import numpy as np
import supersuit as ss
from pettingzoo.atari import warlords_v3
from stable_baselines3 import PPO
from stable_baselines3.common.vec_env import VecMonitor
from stable_baselines3.common.evaluation import evaluate_policy
from pettingzoo.utils.conversions import aec_to_parallel
import gc
import torch  # alleen als je GPU gebruikt

def make_env(num_envs=1): #wrappers
    env = warlords_v3.env(render_mode="rgb_array")
    env = aec_to_parallel(env)
    env = ss.black_death_v3(env)
    env = ss.frame_skip_v0(env, 4)
    env = ss.dtype_v0(env, np.float32)
    env = ss.normalize_obs_v0(env, env_min=0, env_max=255)
    env = ss.pettingzoo_env_to_vec_env_v1(env)
    env = ss.concat_vec_envs_v1(env, num_vec_envs=num_envs, num_cpus=1, base_class="stable_baselines3")
    env = VecMonitor(env)
    return env

def objective(trial):
    print(f"\n=== Start trial {trial.number} ===")
    sys.stdout.flush()

    learning_rate = trial.suggest_loguniform('learning_rate', 1e-5, 1e-3)
    gamma = trial.suggest_uniform('gamma', 0.9, 0.9999)
    ent_coef = trial.suggest_loguniform('ent_coef', 1e-8, 1e-2)
    clip_range = trial.suggest_uniform('clip_range', 0.1, 0.4)

    env = make_env(num_envs=1)

    model = PPO("MlpPolicy", env,  #hyperparameters
                learning_rate=learning_rate,
                gamma=gamma,
                ent_coef=ent_coef,
                clip_range=clip_range,
                verbose=1)

    model.learn(total_timesteps=50_000, progress_bar=True)
    mean_reward, _ = evaluate_policy(model, env, n_eval_episodes=5, warn=False)
    env.close()

    # Opruimen om geheugenlek te voorkomen
    del model
    del env
    gc.collect()
    if torch.cuda.is_available():
        torch.cuda.empty_cache()

    print(f"Trial {trial.number} klaar. Gemiddelde reward: {mean_reward:.2f}")
    sys.stdout.flush()

    return mean_reward

start = time.time()
study = optuna.create_study(direction="maximize")
study.optimize(objective, n_trials=26, catch=(Exception,))

print("\n=== Resultaten ===")
print("Beste hyperparameters:", study.best_params)
print("Beste reward:", study.best_value)
print(f"Totaaltijd: {time.time() - start:.2f} seconden")


[I 2025-06-22 00:26:33,061] A new study created in memory with name: no-name-f5a36631-b622-495b-bf67-e013c67df49a



=== Start trial 0 ===


/tmp/ipython-input-1-2923449848.py:40: FutureWarning: suggest_loguniform has been deprecated in v3.0.0. This feature will be removed in v6.0.0. See https://github.com/optuna/optuna/releases/tag/v3.0.0. Use suggest_float(..., log=True) instead.
  learning_rate = trial.suggest_loguniform('learning_rate', 1e-5, 1e-3)
/tmp/ipython-input-1-2923449848.py:41: FutureWarning: suggest_uniform has been deprecated in v3.0.0. This feature will be removed in v6.0.0. See https://github.com/optuna/optuna/releases/tag/v3.0.0. Use suggest_float instead.
  gamma = trial.suggest_uniform('gamma', 0.9, 0.9999)
/tmp/ipython-input-1-2923449848.py:42: FutureWarning: suggest_loguniform has been deprecated in v3.0.0. This feature will be removed in v6.0.0. See https://github.com/optuna/optuna/releases/tag/v3.0.0. Use suggest_float(..., log=True) instead.
  ent_coef = trial.suggest_loguniform('ent_coef', 1e-8, 1e-2)
/tmp/ipython-input-1-2923449848.py:43: FutureWarning: suggest_uniform has been deprecated in v3.0.

Using cpu device


Output()

...

Trial 7 klaar. Gemiddelde reward: -0.20


[I 2025-06-22 09:40:15,038] Trial 7 finished with value: -0.20000000298023224 and parameters: {'learning_rate': 0.00012392277505010816, 'gamma': 0.9592374109068968, 'ent_coef': 4.282037922149982e-05, 'clip_range': 0.30490417312153706}. Best is trial 3 with value: 0.0.



=== Start trial 8 ===
Using cpu device


Output()

---------------------------------
| rollout/           |          |
|    ep_len_mean     | 1.64e+03 |
|    ep_rew_mean     | -0.5     |
| time/              |          |
|    fps             | 154      |
|    iterations      | 1        |
|    time_elapsed    | 52       |
|    total_timesteps | 8192     |
---------------------------------


In [ ]:
!pip install optuna

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 395.9/395.9 kB 7.3 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 242.7/242.7 kB 18.7 MB/s eta 0:00:00


### Incrementele PPO-training voor Warlords: Single-Agent specialisatie & Generalist-adaptatie

Deze code traint met reinforcement learning één specifieke agent in het multi-agent spel Warlords, terwijl de andere agents random acties uitvoeren. Het model wordt in deze codecell na elke fase opgeslagen en ingeladen. Het model is een PPO (Proximal Policy Optimization); een model waarbij toekomstige beloningen en de advantage van de afgelopen beurten wordt meegerekend terwijl er een clipping wordt gebruikt bij de updates, zodat er minder kans is op overshoots. Het  maakt gebruik van de CnnPolicy, dus in dit model is er een CNN dat beelden verwerkt. Verder vinden er wat preprocessing stappen plaats, zoals kleurreductie, het verkleinen van de plaatjes naar 84x84.

In [ ]:
import numpy as np
import supersuit as ss
from pettingzoo.atari import warlords_v3
from pettingzoo.utils import BaseWrapper
from stable_baselines3 import PPO
from stable_baselines3.common.vec_env import DummyVecEnv, VecMonitor, VecTransposeImage
from stable_baselines3.common.vec_env.vec_frame_stack import VecFrameStack
import os


# 🧠 1. Wrapper om alleen één agent te trainen, rest speelt random
class SingleAgentWrapper(BaseWrapper):
    def __init__(self, env, agent_id):
        super().__init__(env)
        self.agent_id = agent_id

    def reset(self, *args, **kwargs):
        obs = self.env.reset(*args, **kwargs)
        return self.env.observe(self.agent_id)

    def step(self, action):
        for agent in self.env.agent_iter():
            obs, reward, done, info = self.env.last()
            if agent == self.agent_id:
                self.env.step(action)
            else:
                self.env.step(self.env.action_space(agent).sample())

    def render(self, *args, **kwargs):
        return self.env.render(*args, **kwargs)

    def observe(self, agent):
        return self.env.observe(agent)


def make_env(agent_id="first_0"):
    from pettingzoo.utils.conversions import aec_to_parallel

    env = warlords_v3.env()
    env = aec_to_parallel(env)

    env = ss.black_death_v3(env)
    env = ss.color_reduction_v0(env, mode='full')      # nu nog gewoon RGB (3 kanalen)
    env = ss.resize_v1(env, x_size=84, y_size=84)       # werkt nu zonder error
    env = ss.agent_indicator_v0(env, type_only=False)
    env = ss.dtype_v0(env, np.uint8)

    env = ss.pettingzoo_env_to_vec_env_v1(env)
    env = ss.concat_vec_envs_v1(env, num_vec_envs=1, num_cpus=1, base_class="stable_baselines3")

    env = VecFrameStack(env, n_stack=4)
    env = VecTransposeImage(env)
    env = VecMonitor(env)

    print("✅ Observation space:", env.observation_space)
    return env




# 🚀 3. Train de agent
def train_agent(agent_id="first_0", total_timesteps=5000_000, save_path="warlords_10_000.zip"):

    env = make_env(agent_id)

    model = PPO(  #hyperparameters
        "CnnPolicy",
        env,
        verbose=1,
        n_steps=256,  # Kleinere batches voorkomen MemoryError
        batch_size=64,
        device="cuda"  # of "cpu" als je geen GPU hebt
    )

    model.learn(total_timesteps=total_timesteps, progress_bar=True)
    model.save(save_path)
    print(f"✅ Model saved to {save_path}")
    model = PPO.load("warlords_5000_000", env=env)
    model.learn(total_timesteps=5000_000, reset_num_timesteps=False)
    model.save("warlords_10_000_000")
    model = PPO.load("warlords_10_000_000", env=env)
    model.learn(total_timesteps=2500_000, reset_num_timesteps=False)
    model.save("warlords_12_500_000")




#train_agent()


### Gebalanceerde training met willekeurige keuze voor agent

Dit traint een model waarbij telkens 1 van de vier agents wordt gekozen om 250_000 steps mee te trainen.

In [ ]:
import random

def train_generalist_agent(total_timesteps=5_000_000, save_path="warlords_generalist.zip"):
    from stable_baselines3 import PPO

    agent_ids = ["first_0", "second_0", "third_0", "fourth_0"]
    model = None
    timesteps_per_chunk = 250_000  # kleinere stukjes om van agent_id te wisselen

    total_chunks = total_timesteps // timesteps_per_chunk

    for i in range(total_chunks):
        agent_id = random.choice(agent_ids)
        print(f"🔁 Episode {i+1}/{total_chunks} | Training as {agent_id}")

        env = make_env(agent_id)

        if model is None: #hyperparameters
            model = PPO(
                "CnnPolicy",
                env,
                verbose=0,
                n_steps=256,
                batch_size=64,
                device="cuda",  # of "cpu"
            )
        else:
            model.set_env(env)

        model.learn(total_timesteps=timesteps_per_chunk, progress_bar=True)

    model.save(save_path)
    print(f"✅ Generalist model saved to {save_path}")


#train_generalist_agent()

🔁 Episode 1/20 | Training as fourth_0


Output()

/root/miniconda3/envs/pettingzooenv/lib/python3.11/site-packages/stable_baselines3/common/vec_env/base_vec_env.py:78: UserWarning: The `render_mode` attribute is not defined in your environment. It will be set to None.
  warnings.warn("The `render_mode` attribute is not defined in your environment. It will be set to None.")


✅ Observation space: Box(0, 255, (20, 84, 84), uint8)
Using cuda device


-----------------------------
| time/              |      |
|    fps             | 460  |
|    iterations      | 1    |
|    time_elapsed    | 2    |
|    total_timesteps | 1024 |
-----------------------------


...

-------------------------------------------
| rollout/                |               |
|    ep_len_mean          | 7.33e+03      |
|    ep_rew_mean          | -0.5          |
| time/                   |               |
|    fps                  | 236           |
|    iterations           | 242           |
|    time_elapsed         | 1045          |
|    total_timesteps      | 247808        |
| train/                  |               |
|    approx_kl            | 3.6911457e-05 |
|    clip_fraction        | 0             |
|    clip_range           | 0.2           |
|    entropy_loss         | -1.74         |
|    explained_variance   | 1.19e-07      |
|    learning_rate        | 0.0003        |
|    loss                 | -0.00204      |
|    n_updates            | 48960         |
|    policy_gradient_loss | -0.000201     |
|    value_loss           | 2.53e-11      |
-------------------------------------------


-------------------------------------------
| rollout/                |               |
|    ep_len_mean          | 7.33e+03      |
|    ep_rew_mean          | -0.5          |
| time/                   |               |
|    fps                  | 236           |
|    iterations           | 243           |
|    time_elapsed         | 1050          |
|    total_timesteps      | 248832        |
| train/                  |               |
|    approx_kl            | 3.2684475e-05 |
|    clip_fraction        | 0             |
|    clip_range           | 0.2           |
|    entropy_loss         | -1.74         |
|    explained_variance   | 0             |
|    learning_rate        | 0.0003        |
|    loss                 | 0.00402       |
|    n_updates            | 48970         |
|    policy_gradient_loss | -0.000185     |
|    value_loss           | 0.00821       |
-------------------------------------------


-----------------------------------------
| rollout/                |             |
|    ep_len_mean          | 6.94e+03    |
|    ep_rew_mean          | -0.5        |
| time/                   |             |
|    fps                  | 236         |
|    iterations           | 244         |
|    time_elapsed         | 1054        |
|    total_timesteps      | 249856      |
| train/                  |             |
|    approx_kl            | 8.21086e-05 |
|    clip_fraction        | 0           |
|    clip_range           | 0.2         |
|    entropy_loss         | -1.74       |
|    explained_variance   | 5.96e-08    |
|    learning_rate        | 0.0003      |
|    loss                 | 0.000739    |
|    n_updates            | 48980       |
|    policy_gradient_loss | -0.000423   |
|    value_loss           | 8.26e-07    |
-----------------------------------------


------------------------------------------
| rollout/                |              |
|    ep_len_mean          | 6.94e+03     |
|    ep_rew_mean          | -0.5         |
| time/                   |              |
|    fps                  | 236          |
|    iterations           | 245          |
|    time_elapsed         | 1058         |
|    total_timesteps      | 250880       |
| train/                  |              |
|    approx_kl            | 5.439832e-05 |
|    clip_fraction        | 0            |
|    clip_range           | 0.2          |
|    entropy_loss         | -1.74        |
|    explained_variance   | 5.96e-08     |
|    learning_rate        | 0.0003       |
|    loss                 | 0.0068       |
|    n_updates            | 48990        |
|    policy_gradient_loss | -0.000333    |
|    value_loss           | 0.0249       |
------------------------------------------


✅ Generalist model saved to warlords_generalist.zip


Traint een agent verder, omdat het model zo stapsgewijs kan verbeteren zonder eerdere kennis te verliezen en flexibel tussentijds kan worden aangepast of gepauzeerd.

In [ ]:
# 🚀 3. Train de agent
def continue_training(agent_id="first_0", total_timesteps=1000_000):

    env = make_env(agent_id)


    model = PPO.load("warlords_single_agent", env=env)
    model.learn(total_timesteps=1000_000, reset_num_timesteps=False)
    model.save("warlords_single_agent_2M")
    print("Model warlords_single_agent_2M is getrained")
    model = PPO.load("warlords_single_agent_2M", env=env)
    model.learn(total_timesteps=1000_000, reset_num_timesteps=False)
    model.save("warlords_single_agent_3M")
    print("Model warlords_single_agent_2M is getrained")




continue_training()

/root/miniconda3/envs/pettingzooenv/lib/python3.11/site-packages/stable_baselines3/common/vec_env/base_vec_env.py:78: UserWarning: The `render_mode` attribute is not defined in your environment. It will be set to None.
  warnings.warn("The `render_mode` attribute is not defined in your environment. It will be set to None.")


✅ Observation space: Box(0, 255, (20, 84, 84), uint8)
---------------------------------
| rollout/           |          |
|    ep_len_mean     | 8.88e+03 |
|    ep_rew_mean     | -0.5     |
| time/              |          |
|    fps             | 520      |
|    iterations      | 1        |
|    time_elapsed    | 1        |
|    total_timesteps | 1001472  |
---------------------------------
----------------------------------------
| rollout/                |            |
|    ep_len_mean          | 8.88e+03   |
|    ep_rew_mean          | -0.5       |
| time/                   |            |
|    fps                  | 316        |
|    iterations           | 2          |
|    time_elapsed         | 6          |
|    total_timesteps      | 1002496    |
| train/                  |            |
|    approx_kl            | 0.05174488 |
|    clip_fraction        | 0.161      |
|    clip_range           | 0.2        |
|    entropy_loss         | -1.49      |
|    explained_variance   | -1.2